In [2]:
import pandas as pd
import numpy as np

In [4]:
#Loading in data from stored csvs created in feature engineering notebook
pop_df = pd.read_csv("stations_populations.csv")
paths_df = pd.read_csv("shortest_paths.csv")
stations = np.array(pd.read_csv("stations.csv")['station'])
total_pop = np.array(pop_df.Population).sum()

In [7]:
#translating shortest path times into a dictionary to speed up accessing
paths_dict = {}
for i in range(len(paths_df)):
    if not paths_df['Station 1'][i] in paths_dict.keys():
        paths_dict[paths_df['Station 1'][i]] = {}
    paths_dict[paths_df['Station 1'][i]][paths_df['Station 2'][i]] = paths_df['Time'][i]
paths_dict

{'12th Street': {'12th Street': 0,
  '16th Street Mission': 1140,
  '19th Street': 120,
  '24th Street Mission': 1260,
  'Antioch': 3480,
  'Ashby': 540,
  'Balboa Park': 1560,
  'Bay Fair': 1200,
  'Berryessa': 3480,
  'Castro Valley': 1494,
  'Civic Center': 960,
  'Coliseum': 720,
  'Colma': 2040,
  'Concord': 1920,
  'Daly City': 1800,
  'Downtown Berkeley': 720,
  'Dublin': 2274,
  'El Cerrito del Norte': 1200,
  'El Cerrito Plaza': 1020,
  'Embarcadero': 720,
  'Fremont': 2280,
  'Fruitvale': 480,
  'Glen Park': 1440,
  'Hayward': 1440,
  'Lafayette': 1140,
  'Lake Merritt': 180,
  'MacArthur': 300,
  'Millbrae': 2880,
  'Milpitas': 3180,
  'Montgomery Street': 780,
  'North Berkeley': 840,
  'North Concord': 2100,
  'OAK': 1254,
  'Orinda': 840,
  'Pittsburg': 2460,
  'Pittsburg Center': 3060,
  'Pleasant Hill': 1560,
  'Powell Street': 900,
  'Richmond': 1500,
  'Rockridge': 540,
  'San Bruno': 2460,
  'San Leandro': 960,
  'SFO': 2700,
  'South Hayward': 1680,
  'South San Fra

In [49]:
#same thing for populations
pop_dict = {}
for i in range(len(pop_df['Station'])):
    pop_dict[pop_df['Station'][i]] = pop_df['Population'][i]
for i in range(len(stations)):
    if not stations[i] in pop_dict.keys():
        pop_dict[stations[i]] = 0
pop_dict

{'16th Street Mission': 78993,
 '19th Street': 47558,
 '24th Street Mission': 109524,
 'Antioch': 66933,
 'Balboa Park': 106589,
 'Bay Fair': 93041,
 'Berryessa': 166470,
 'Castro Valley': 44272,
 'Civic Center': 177424,
 'Coliseum': 36148,
 'Colma': 114402,
 'Concord': 28428,
 'Daly City': 31488,
 'Downtown Berkeley': 65838,
 'Dublin': 54420,
 'El Cerrito Plaza': 32956,
 'El Cerrito del Norte': 39962,
 'Embarcadero': 15839,
 'Fremont': 73855,
 'Fruitvale': 52299,
 'Glen Park': 72373,
 'Hayward': 66056,
 'Lafayette': 29639,
 'Lake Merritt': 102146,
 'MacArthur': 53100,
 'Millbrae': 22710,
 'Milpitas': 31170,
 'Montgomery Street': 48914,
 'North Berkeley': 36008,
 'North Concord': 58689,
 'OAK': 14619,
 'Orinda': 19341,
 'Pittsburg Center': 96081,
 'Pleasant Hill': 35096,
 'Powell Street': 29689,
 'Richmond': 71468,
 'Rockridge': 30406,
 'SFO': 135,
 'San Bruno': 110721,
 'San Leandro': 82681,
 'South Hayward': 93452,
 'South San Francisco': 4692,
 'Union City': 74601,
 'Walnut Creek': 

In [87]:
#helper functions used to calculate the weighted average arrival time for every combination of n stations

def get_average_time(distribution_centers):
    output = 0
    worst_best = -np.inf
    for station in stations:
        best_time = np.inf
        for dc in distribution_centers:
            time = paths_dict[dc][station]
            best_time = min(best_time, time)
        output += best_time * pop_dict[station]
        worst_best = max(worst_best, best_time)
    return output / total_pop, worst_best

#didn't actually work out to be faster
"""def get_average_time_enhanced(distribution_centers):
    times = []
    pops = []
    for dc in distribution_centers:
        times.append(list(paths_dict[dc].values()))
    times = np.stack(times, axis = -1)
    idx = np.argmin(times, axis = 1)
    idx_1 = range(len(times))
    best_times = times[idx_1, idx]
    return (best_times * pop_array).sum() / total_pop, best_times.max()"""

def get_all_combinations(n):
    output = []
    for i in range(len(stations)):
        output += get_all_stations_helper(i, [stations[i]], 1, n)
        
    combos = []
    for i in range(n):
        combos.append(output[i::n])
    return np.stack(combos, axis = 1)
    
def get_all_stations_helper(i, l, depth, maximum_depth):
    if maximum_depth <= depth:
        return l
    output = []
    for j in range(i + 1, len(stations)):
        output += get_all_stations_helper(j, l + [stations[j]], depth + 1, maximum_depth)
    
    return output

def get_distribution_center_optimality(num_centers):
    combos = get_all_combinations(num_centers)
    avg_time = []
    worst_cases = []
    for i in range(len(combos)):
        t, wb = get_average_time(combos[i])
        avg_time.append(t)
        worst_cases.append(wb)
        print(i/len(combos)*100, end = "\r")
        
    dc_optimality = {}
    for i in range(num_centers):
        dc_optimality["Distribution Center " + str(i)] = combos[:,i]
    dc_optimality['Average Arrival Time'] = avg_time
    dc_optimality['Worst Case Arrival Time'] = worst_cases
    
    return pd.DataFrame(dc_optimality).sort_values(["Average Arrival Time"])

In [94]:
#Running the numbers
output_df = get_distribution_center_optimality(4)

48.08423795049935

58.99088145896657

68.5601389491967

68.88623534520191

71.5670864090317

72.23751628310899

In [95]:
#Displaying results
output_df

Distribution Center 0 Distribution Center 1 Distribution Center 2  \
105023           Balboa Park             MacArthur      Pittsburg Center   
102968           Balboa Park               Fremont             MacArthur   
105021           Balboa Park             MacArthur      Pittsburg Center   
104022           Balboa Park               Hayward             MacArthur   
176073             Daly City             MacArthur      Pittsburg Center   
...                      ...                   ...                   ...   
185513                Dublin               Fremont              Milpitas   
123361             Berryessa                Dublin              Milpitas   
70420                Antioch             Berryessa              Milpitas   
125163             Berryessa               Fremont              Milpitas   
80369                Antioch         North Concord             Pittsburg   

       Distribution Center 3  Average Arrival Time  Worst Case Arrival Time  
105023            Union City            676.769107                     1863  
102968      Pittsburg Center            677.866950                     2163  
105021         South Hayward            678.517399                     1800  
104022      Pittsburg Center            678.849187                     2040  
176073            Union City            685.244159                     1863  
...                      ...                   ...                      ...  
185513          Warm Springs           2892.724391                     5813  
123361          Warm Springs           2905.080090                     5813  
70420       Pittsburg Center           2925.819054                     5988  
125163          Warm Springs           2940.632242                     5819  
80369       Pittsburg Center           3021.104262                     5639  

[230300 rows x 6 columns]